# Conectando ao MongoDB usando Python

In [1]:
from pymongo import MongoClient
from pprintpp import pprint
import warnings
warnings.filterwarnings('ignore')

In [2]:
mongoclient = MongoClient('localhost', 27017)
db = mongoclient.thedatasocietydb
print(db)

Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'thedatasocietydb')


# CRUD MongoDB usando Python

## Create - insert()

* Não há regras de validação rígidas: qualquer tipo de documento pode ser armazenado no banco de dados. 

* Na prática, somente objetos semelhantes são armazenados na base de dados, porém se um dia aparecer um novo atributo, poderemos inclui-lo apenas nos documentos aonde o mesmo é necessário, ao contrário do modelo relacional, onde uma nova coluna seria necessária e seria aplicada a todos os registros.

* Desvantagem: 

    * Cuidado para que as bases de dados não virem uma grande confusão (vão virar, aceite desde o início)
    
    
* Vantagens:

    * Temos uma abordagem n-dimensional para representar objetos (bem… o mundo muda)
    
    * Facilidade de alteração da estrutura de dados (refatoração fria)



In [3]:
# Insere um documento na coleção autores
documento1 = {
              "idade": 25,
              "nome":"Joao"
             }

db.autores.insert_one(documento1)

ObjectId('5f2e29cab7f5ee4d9e5cb838')

In [4]:
#Insere outro documento com estrutura diferente em autores

db.autores.insert_one(
                  {
                    "nome": "Joaquim",
                    "idade": 30,
                    "cidade": "Campinas"
                  }
)

ObjectId('5f2e29cab7f5ee4d9e5cb839')

In [5]:
# Insere outro documento com estrutura diferente em autores

db.autores.insert_one(
                  {
                   "nome": "Maria",
                   "poemaPreferido": "Desejo – Victor Hugo",
                   "familia":{
                              "pai": "Isaac Mato",
                              "mae": "Junia Lito"
                             }
                  }

)

ObjectId('5f2e29cab7f5ee4d9e5cb83a')

In [6]:
# Insere documento com estrutura diferente que possui outro documento (publicacao) embutido (embedded)

db.autores.insert_one(
                  {
                   "nome": "Horacio",
                   "cidade": "Campinas",                      
                   "publicacao_principal": {    
                                            "tipo": "livro",
                                            "titulo": "Vida dos Dinossauros",
                                            "ano": 2010
                                           },
                    "familia": {
                                "pai": "Joao Silva",
                                "mae": "Marta Figo"
                               }
                  }
)

ObjectId('5f2e29cab7f5ee4d9e5cb83b')

In [7]:
# Insere outro documento que possui outro documento (publicacao) embutido (embedded)

db.autores.insert_one(
                  {
                   "nome": "Tenario",
                   "cidade": "Campinas",                      
                   "publicacao_principal": {    
                                            "tipo": "artigo",
                                            "titulo": "Ser ou não ser?",
                                            "ano": 1874
                                           },
                    "familia": {
                                "pai": "Tulio Primeiro",
                                "mae": "Algonia Kino"
                               }
                  }
)

ObjectId('5f2e29cab7f5ee4d9e5cb83c')

###  insert_many()

In [8]:
db.inventory.insert_many(
                         [
                          { "item": "journal", "qty": 25, "tags": ["blank", "red"], "size": { "h": 14,   "w": 21,    "uom": "cm" } },
                          { "item": "mat",     "qty": 85, "tags": ["gray"],         "size": { "h": 27.9, "w": 35.5,  "uom": "cm" } },
                          { "item": "mousepad","qty": 25, "tags": ["gel", "blue"],  "size": { "h": 19,   "w": 22.85, "uom": "cm" } }
                         ])
# usar .inserted_ids no objeto de retorno para saber os ids inseridos

### Alterando o _id

<img src="../../resources/images/oid.png" width="50%">

<img src="../../resources/images/oid2.png" width="50%">

In [9]:
db.autores.insert_one({ 
                   "_id": "autor-14", 
                   "nome": "Malaquias", 
                   "cidade": "Campinas",
                   "idade": 78 
                  } 
)

'autor-14'

In [10]:
result = db.autores.find({"autor": "Malaquias"})
list(result)

[]

## Find

<img src="../../resources/images/find.png" width="50%"> 

In [11]:
# Lista todos os documentos da coleção autores usando Mongo Shell

! mongo --quiet --eval 'db.autores.find({});' thedatasocietydb

{ "_id" : ObjectId("5f2e29cab7f5ee4d9e5cb838"), "idade" : 25, "nome" : "Joao" }
{ "_id" : ObjectId("5f2e29cab7f5ee4d9e5cb839"), "nome" : "Joaquim", "idade" : 30, "cidade" : "Campinas" }
{ "_id" : ObjectId("5f2e29cab7f5ee4d9e5cb83a"), "nome" : "Maria", "poemaPreferido" : "Desejo – Victor Hugo", "familia" : { "pai" : "Isaac Mato", "mae" : "Junia Lito" } }
{ "_id" : ObjectId("5f2e29cab7f5ee4d9e5cb83b"), "nome" : "Horacio", "cidade" : "Campinas", "publicacao_principal" : { "tipo" : "livro", "titulo" : "Vida dos Dinossauros", "ano" : 2010 }, "familia" : { "pai" : "Joao Silva", "mae" : "Marta Figo" } }
{ "_id" : ObjectId("5f2e29cab7f5ee4d9e5cb83c"), "nome" : "Tenario", "cidade" : "Campinas", "publicacao_principal" : { "tipo" : "artigo", "titulo" : "Ser ou não ser?", "ano" : 1874 }, "familia" : { "pai" : "Tulio Primeiro", "mae" : "Algonia Kino" } }
{ "_id" : "autor-14", "nome" : "Malaquias", "cidade" : "Campinas", "idade" : 78 }


In [12]:
# Lista todos os documentos da coleção autores usando Python

result = db.autores.find()

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb838'), 'idade': 25, 'nome': 'Joao'},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb839'),
  'nome': 'Joaquim',
  'idade': 30,
  'cidade': 'Campinas'},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
  'nome': 'Maria',
  'poemaPreferido': 'Desejo – Victor Hugo',
  'familia': {'pai': 'Isaac Mato', 'mae': 'Junia Lito'}},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83b'),
  'nome': 'Horacio',
  'cidade': 'Campinas',
  'publicacao_principal': {'tipo': 'livro',
   'titulo': 'Vida dos Dinossauros',
   'ano': 2010},
  'familia': {'pai': 'Joao Silva', 'mae': 'Marta Figo'}},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83c'),
  'nome': 'Tenario',
  'cidade': 'Campinas',
  'publicacao_principal': {'tipo': 'artigo',
   'titulo': 'Ser ou não ser?',
   'ano': 1874},
  'familia': {'pai': 'Tulio Primeiro', 'mae': 'Algonia Kino'}},
 {'_id': 'autor-14', 'nome': 'Malaquias', 'cidade': 'Campinas', 'idade': 78}]

In [13]:
# Lista todos os documentos da coleção autores

result = db.autores.find()

# usando a função pretty print
pprint( list(result) )

[
    {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb838'), 'idade': 25, 'nome': 'Joao'},
    {
        '_id': ObjectId('5f2e29cab7f5ee4d9e5cb839'),
        'cidade': 'Campinas',
        'idade': 30,
        'nome': 'Joaquim',
    },
    {
        '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
        'familia': {'mae': 'Junia Lito', 'pai': 'Isaac Mato'},
        'nome': 'Maria',
        'poemaPreferido': 'Desejo – Victor Hugo',
    },
    {
        '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83b'),
        'cidade': 'Campinas',
        'familia': {'mae': 'Marta Figo', 'pai': 'Joao Silva'},
        'nome': 'Horacio',
        'publicacao_principal': {
            'ano': 2010,
            'tipo': 'livro',
            'titulo': 'Vida dos Dinossauros',
        },
    },
    {
        '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83c'),
        'cidade': 'Campinas',
        'familia': {'mae': 'Algonia Kino', 'pai': 'Tulio Primeiro'},
        'nome': 'Tenario',
        'publicacao_principal': {
            'ano': 1

### Condição de igualdade


In [14]:
# Lista os documentos de autores com nome = Maria

result = db.autores.find({"nome": "Maria"})

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
  'nome': 'Maria',
  'poemaPreferido': 'Desejo – Victor Hugo',
  'familia': {'pai': 'Isaac Mato', 'mae': 'Junia Lito'}}]

In [15]:
# Lista poemaPreferido de documentos de autores com nome = Maria

result = db.autores.find(
                         {
                             "nome": "Maria"
                         }, 
                         {
                             "_id": 0,
                             "nome":1,
                             "poemaPreferido": 1
                         }
                    )

list(result)

[{'nome': 'Maria', 'poemaPreferido': 'Desejo – Victor Hugo'}]

In [16]:
# Lista documentos de autores com tipo da publicacao = livro

result = db.autores.find({"publicacao_principal.tipo": "livro"})

# list(result)  
pprint( list(result))

[
    {
        '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83b'),
        'cidade': 'Campinas',
        'familia': {'mae': 'Marta Figo', 'pai': 'Joao Silva'},
        'nome': 'Horacio',
        'publicacao_principal': {
            'ano': 2010,
            'tipo': 'livro',
            'titulo': 'Vida dos Dinossauros',
        },
    },
]


In [17]:
# Documentos de autores com tipo = livro e ano entre 2000 e 2015

result = db.autores.find(
                          {
                            "publicacao_principal.tipo": {"$in":["artigo","livro"]},
                            "publicacao_principal.ano": {"$gt": 1500, "$lt": 2016}
                          }
                        )
for document in result: 
    pprint(document)

{
    '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83b'),
    'cidade': 'Campinas',
    'familia': {'mae': 'Marta Figo', 'pai': 'Joao Silva'},
    'nome': 'Horacio',
    'publicacao_principal': {
        'ano': 2010,
        'tipo': 'livro',
        'titulo': 'Vida dos Dinossauros',
    },
}
{
    '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83c'),
    'cidade': 'Campinas',
    'familia': {'mae': 'Algonia Kino', 'pai': 'Tulio Primeiro'},
    'nome': 'Tenario',
    'publicacao_principal': {
        'ano': 1874,
        'tipo': 'artigo',
        'titulo': 'Ser ou não ser?',
    },
}


### Operadores Lógicos

In [18]:
result = db.autores.find(
                          {
                            "$or": [ 
                                    { "publicacao_principal.ano": {"$gt" : 1999, "$lt": 2016} }, 
                                    { "publicacao_principal.ano": {"$gte": 1980, "$lt": 1991} } 
                                   ] 
                          }
)

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83b'),
  'nome': 'Horacio',
  'cidade': 'Campinas',
  'publicacao_principal': {'tipo': 'livro',
   'titulo': 'Vida dos Dinossauros',
   'ano': 2010},
  'familia': {'pai': 'Joao Silva', 'mae': 'Marta Figo'}}]

In [19]:
result = db.autores.find({"idade" : {"$in" : [25, 42, 80]}})

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb838'), 'idade': 25, 'nome': 'Joao'}]

In [20]:
result = db.autores.find({"$or" : [
                                   {"idade" : {"$in" : [25, 42, 80] } },
                                   {"cidade": "Campinas"}
                                  ]
                         }
)
list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb838'), 'idade': 25, 'nome': 'Joao'},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb839'),
  'nome': 'Joaquim',
  'idade': 30,
  'cidade': 'Campinas'},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83b'),
  'nome': 'Horacio',
  'cidade': 'Campinas',
  'publicacao_principal': {'tipo': 'livro',
   'titulo': 'Vida dos Dinossauros',
   'ano': 2010},
  'familia': {'pai': 'Joao Silva', 'mae': 'Marta Figo'}},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83c'),
  'nome': 'Tenario',
  'cidade': 'Campinas',
  'publicacao_principal': {'tipo': 'artigo',
   'titulo': 'Ser ou não ser?',
   'ano': 1874},
  'familia': {'pai': 'Tulio Primeiro', 'mae': 'Algonia Kino'}},
 {'_id': 'autor-14', 'nome': 'Malaquias', 'cidade': 'Campinas', 'idade': 78}]

### Operadores de Elementos

In [21]:
result = db.autores.find(
                          {
                            "poemaPreferido": { "$exists": True}
                          }
                        )
print( list(result) )

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'), 'nome': 'Maria', 'poemaPreferido': 'Desejo – Victor Hugo', 'familia': {'pai': 'Isaac Mato', 'mae': 'Junia Lito'}}]


### Count

In [22]:
db.autores.count_documents({})

6

In [23]:
db.autores.count_documents({"nome":"Horacio"})

1

### Limit

In [24]:
result = db.autores.find({}).limit(2)

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb838'), 'idade': 25, 'nome': 'Joao'},
 {'_id': ObjectId('5f2e29cab7f5ee4d9e5cb839'),
  'nome': 'Joaquim',
  'idade': 30,
  'cidade': 'Campinas'}]

### Distinct


In [25]:
result = db.autores.distinct("nome")
list(result)

['Horacio', 'Joao', 'Joaquim', 'Malaquias', 'Maria', 'Tenario']

In [26]:
result = db.autores.distinct("publicacao_principal.titulo")
list(result)

['Ser ou não ser?', 'Vida dos Dinossauros']

In [27]:
result = db.autores.find({"cidade":"Campinas"}).distinct("nome")
list(result)

['Horacio', 'Joaquim', 'Malaquias', 'Tenario']

## Update

In [28]:
# Atualiza cidade de autor = Joaquim

db.autores.update_one(
                   { "nome" : "Joaquim" },
                   { "$set": { 
                               "cidade": "Ilheus" 
                             } 
                   }
)


{'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}

In [29]:
result = db.autores.find({ "nome" : "Joaquim" })

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb839'),
  'nome': 'Joaquim',
  'idade': 30,
  'cidade': 'Ilheus'}]

In [30]:
result = db.autores.find({ "nome" : "Maria" })

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
  'nome': 'Maria',
  'poemaPreferido': 'Desejo – Victor Hugo',
  'familia': {'pai': 'Isaac Mato', 'mae': 'Junia Lito'}}]

In [31]:
# Adiciona atributo cidade ao autor de nome = Maria

db.autores.update_one(
                    {"nome": "Maria"}, 
                    {"$set": {"cidade": "Campinas"}}
)

{'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}

In [32]:
result = db.autores.find({ "nome" : "Maria" })

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
  'nome': 'Maria',
  'poemaPreferido': 'Desejo – Victor Hugo',
  'familia': {'pai': 'Isaac Mato', 'mae': 'Junia Lito'},
  'cidade': 'Campinas'}]

In [33]:
# Exclui atributo poemaPreferido ao autor de nome = Maria
db.autores.update_one(
                    {"nome": "Maria"}, 
                    {"$unset": {"poemaPreferido": 1}}
)

{'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}

In [34]:
result = db.autores.find({ "nome" : "Maria" })

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
  'nome': 'Maria',
  'familia': {'pai': 'Isaac Mato', 'mae': 'Junia Lito'},
  'cidade': 'Campinas'}]

In [36]:
result = db.autores.find({ "nome" : "Maria" })

list(result)

[{'_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
  'nome': 'Maria',
  'poemaPreferido': 'Desejo – Victor Hugo',
  'publicacao_principal': {'tipo': 'livro',
   'titulo': 'Vida dos Dinossauros',
   'ano': 2014}}]

### Operadores Update

* **upsert**: Opcional. Se = true, cria um novo documento quando não encontra um que atende ao critério de busca. Default = false.

* **multi:** Opcional. Se = true, atualiza todos os documentos que atendem ao critério de busca. Se = false, atualiza apenas o primeiro documento. Default = false.

In [37]:
# Atualiza todos os documentos com titulo Vida dos Dinossauros
db.autores.update_one(
                  { "publicacao_principal.titulo":"Vida dos Dinossauros"},
                  { "$set": {"publicacao_principal.ano": 2020}},
                  upsert=False, 
                  multi=True  
)

{'n': 2, 'nModified': 2, 'ok': 1.0, 'updatedExisting': True}

In [38]:
result = db.autores.find({ "publicacao_principal.titulo" : "Vida dos Dinossauros" })

pprint( list(result) )

[
    {
        '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83a'),
        'nome': 'Maria',
        'poemaPreferido': 'Desejo – Victor Hugo',
        'publicacao_principal': {
            'ano': 2020,
            'tipo': 'livro',
            'titulo': 'Vida dos Dinossauros',
        },
    },
    {
        '_id': ObjectId('5f2e29cab7f5ee4d9e5cb83b'),
        'cidade': 'Campinas',
        'familia': {'mae': 'Marta Figo', 'pai': 'Joao Silva'},
        'nome': 'Horacio',
        'publicacao_principal': {
            'ano': 2020,
            'tipo': 'livro',
            'titulo': 'Vida dos Dinossauros',
        },
    },
]


## Remove

In [39]:
db.autores.count()

6

In [40]:
# Exclui documento cujo autor = Maria

db.autores.remove({"nome": "Maria"})

{'n': 1, 'ok': 1.0}

In [41]:
db.autores.count()

5

In [42]:
# Exclui todos os documentos da coleção

# db.autores.remove({})